In [1]:
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras import optimizers
import tensorflow as tf
from tensorflow.keras.layers import Dense, Activation, Flatten, Dropout
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error 
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np
from sklearn import metrics
import seaborn as sns
from tensorflow.keras.optimizers.experimental import AdamW
from sklearn.model_selection import KFold, StratifiedKFold

In [2]:
data_path = 'data.csv'
df = pd.read_csv(data_path)

In [3]:
df.head()

Layer-1 Layer-2  Ana-1  Ana-2  Thickness  WaveLength  Core_Real  \
0      Au    TiO2   1.33   1.33         40      1500.0     1.4327   
1      Au    TiO2   1.33   1.33         40      1520.0     1.4322   
2      Au    TiO2   1.33   1.33         40      1540.0     1.4316   
3      Au    TiO2   1.33   1.33         40      1560.0     1.4311   
4      Au    TiO2   1.33   1.33         40      1580.0     1.4305   

       CoreImag    TotalPower     CorePower  EffectiveArea   EML    CLoss  
0 -3.380000e-09  5.240000e-10  5.230000e-10   1.940000e-11  19.9  0.12289  
1 -4.400000e-09  5.030000e-10  5.010000e-10   1.660000e-11  19.9  0.15782  
2 -5.840000e-09  4.960000e-10  4.940000e-10   1.570000e-11  19.9  0.20700  
3 -8.070000e-09  4.930000e-10  4.920000e-10   1.650000e-11  19.9  0.28230  
4 -1.190000e-08  4.630000e-10  4.620000e-10   1.990000e-11  19.9  0.41038

In [4]:
df.shape

(5527, 13)

In [5]:
dummy_fields = ["Layer-1","Layer-2"]

for each in dummy_fields:
    dummies = pd.get_dummies(df[each], prefix=each, drop_first=False)
    df = pd.concat([df,dummies], axis=1)

In [6]:
fields_to_drop = ["Layer-1","Layer-2"]
df = df.drop(fields_to_drop, axis=1)

In [7]:
df.head()

Ana-1  Ana-2  Thickness  WaveLength  Core_Real      CoreImag    TotalPower  \
0   1.33   1.33         40      1500.0     1.4327 -3.380000e-09  5.240000e-10   
1   1.33   1.33         40      1520.0     1.4322 -4.400000e-09  5.030000e-10   
2   1.33   1.33         40      1540.0     1.4316 -5.840000e-09  4.960000e-10   
3   1.33   1.33         40      1560.0     1.4311 -8.070000e-09  4.930000e-10   
4   1.33   1.33         40      1580.0     1.4305 -1.190000e-08  4.630000e-10   

      CorePower  EffectiveArea   EML    CLoss  Layer-1_AU  Layer-1_Au  \
0  5.230000e-10   1.940000e-11  19.9  0.12289           0           1   
1  5.010000e-10   1.660000e-11  19.9  0.15782           0           1   
2  4.940000e-10   1.570000e-11  19.9  0.20700           0           1   
3  4.920000e-10   1.650000e-11  19.9  0.28230           0           1   
4  4.620000e-10   1.990000e-11  19.9  0.41038           0           1   

   Layer-1_Au+Ta2O5  Layer-1_TiO2  Layer-2_Au  Layer-2_TIO2  Layer-2_Ta2O5  \
0                 0             0           0             0              0   
1                 0             0           0             0              0   
2                 0             0           0             0              0   
3                 0             0           0             0              0   
4                 0             0           0             0              0   

   Layer-2_TiO2  
0             1  
1             1  
2             1  
3             1  
4             1

In [8]:
for each in df.columns:
  print(each,' '*(20-len(each)), df[each].isnull().values.any())

Ana-1                 False
Ana-2                 False
Thickness             False
WaveLength            False
Core_Real             False
CoreImag              False
TotalPower            False
CorePower             False
EffectiveArea         False
EML                   False
CLoss                 False
Layer-1_AU            False
Layer-1_Au            False
Layer-1_Au+Ta2O5      False
Layer-1_TiO2          False
Layer-2_Au            False
Layer-2_TIO2          False
Layer-2_Ta2O5         False
Layer-2_TiO2          False


In [9]:
tar = ['Core_Real', 'CoreImag', 'TotalPower', 'CorePower','EML', 'CLoss']
# tar = ['CLoss']
x = df[["Layer-1_Au",	"Layer-1_Au+Ta2O5",	"Layer-1_TiO2",	"Layer-2_Au",	"Layer-2_Ta2O5",	"Layer-2_TiO2","Ana-1","Ana-2","Thickness","WaveLength"]]
y = df[tar]

In [10]:
x.head()

Layer-1_Au  Layer-1_Au+Ta2O5  Layer-1_TiO2  Layer-2_Au  Layer-2_Ta2O5  \
0           1                 0             0           0              0   
1           1                 0             0           0              0   
2           1                 0             0           0              0   
3           1                 0             0           0              0   
4           1                 0             0           0              0   

   Layer-2_TiO2  Ana-1  Ana-2  Thickness  WaveLength  
0             1   1.33   1.33         40      1500.0  
1             1   1.33   1.33         40      1520.0  
2             1   1.33   1.33         40      1540.0  
3             1   1.33   1.33         40      1560.0  
4             1   1.33   1.33         40      1580.0

In [11]:
quant_features = tar
scaled_features = {}

for each in quant_features:
    mean, std = y[each].mean(), y[each].std()
    scaled_features[each] = [mean, std]
    y.loc[:, each] = (y[each] - mean)/std 

C:\Users\Administrator\AppData\Local\Temp\ipykernel_9576\3167035514.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y.loc[:, each] = (y[each] - mean)/std
C:\Users\Administrator\AppData\Local\Temp\ipykernel_9576\3167035514.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y.loc[:, each] = (y[each] - mean)/std
C:\Users\Administrator\AppData\Local\Temp\ipykernel_9576\3167035514.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col

In [12]:
X_train, X_test, y_train, y_test = train_test_split(x,y,test_size=0.2, random_state=45)

In [13]:
X_train = X_train.to_numpy()
y_train = y_train.to_numpy()
X_test = X_test.to_numpy()
y_test = y_test.to_numpy()

In [14]:
X_train[0:5,:]

array([[1.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 1.00e+00,
        1.35e+00, 1.34e+00, 4.00e+01, 1.56e+03],
       [0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00,
        1.30e+00, 1.30e+00, 3.50e+01, 1.74e+03],
       [0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00,
        1.30e+00, 1.34e+00, 3.50e+01, 2.00e+03],
       [1.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 1.00e+00,
        1.36e+00, 1.39e+00, 4.00e+01, 1.60e+03],
       [1.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00, 1.00e+00,
        1.37e+00, 1.33e+00, 4.00e+01, 1.94e+03]])

In [15]:
y_train[0:5,:]

array([[ 0.93622996,  0.31624331,  0.66717191,  0.67116436,  0.70299499,
        -0.32842529],
       [ 0.79642073,  0.31085113,  0.28582925,  0.29048972, -0.78102361,
        -0.32158693],
       [-0.74148081,  0.22358526, -0.59291687, -0.59499259, -0.78102361,
        -0.21952878],
       [ 0.79642073,  0.31502497,  0.52624093,  0.52220471,  0.61938831,
        -0.32675162],
       [-0.48728221,  0.2515663 , -0.61778704, -0.6198192 , -0.38389187,
        -0.2503372 ]])

In [37]:
model = Sequential()

model.add(Dense(256, kernel_initializer='normal', input_dim = 10, activation='relu'))

model.add(Dense(128, kernel_initializer='normal', activation='relu'))

model.add(Dense(64, kernel_initializer='normal', activation='relu'))

model.add(Dense(32, kernel_initializer='normal', activation='relu'))

model.add(Dense(16, kernel_initializer='normal', activation='relu'))

model.add(Dense(6, kernel_initializer='normal', activation='linear'))

# opt = optimizers.RMSprop(
#     learning_rate=0.0001,
#     rho=0.9,
#     momentum=0.0,
#     epsilon=1e-07,
#     centered=False,
# )

# schedule = tf.optimizers.schedules.PiecewiseConstantDecay(
#         [5000,15000], [1e-4, 1e-4, 1e-5])
# optimizer = tf.keras.optimizers.Adam(learning_rate=schedule)



In [38]:
schedule = tf.optimizers.schedules.PiecewiseConstantDecay(
        [300, 14000,45000], [0.001, 0.0001,0.00001,0.000001])
ada = optimizers.Adam(
    learning_rate=schedule,
    beta_1=0.9,
    beta_2=0.999,
    epsilon=1e-07,
    amsgrad=False,
    name="Adam"
)

model.compile(loss='mse', optimizer=ada, metrics=['mae', 'mse'])
model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_12 (Dense)            (None, 256)               2816      
                                                                 
 dense_13 (Dense)            (None, 128)               32896     
                                                                 
 dense_14 (Dense)            (None, 64)                8256      
                                                                 
 dense_15 (Dense)            (None, 32)                2080      
                                                                 
 dense_16 (Dense)            (None, 16)                528       
                                                                 
 dense_17 (Dense)            (None, 6)                 102       
                                                                 
Total params: 46,678
Trainable params: 46,678
Non-trai

In [ ]:
history = model.fit(
    X_train, 
    y_train, 
    epochs=60000, 
    batch_size=64, 
    validation_split = 0.2)

Epoch 1/60000
56/56 [==============================] - 1s 3ms/step - loss: 0.9974 - mae: 0.6797 - mse: 0.9974 - val_loss: 1.0491 - val_mae: 0.6816 - val_mse: 1.0491
Epoch 2/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.9867 - mae: 0.6719 - mse: 0.9867 - val_loss: 1.0365 - val_mae: 0.6565 - val_mse: 1.0365
Epoch 3/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.9752 - mae: 0.6678 - mse: 0.9752 - val_loss: 1.0221 - val_mae: 0.6534 - val_mse: 1.0221
Epoch 4/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.9542 - mae: 0.6582 - mse: 0.9542 - val_loss: 1.0209 - val_mae: 0.6830 - val_mse: 1.0209
Epoch 5/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.9074 - mae: 0.6419 - mse: 0.9074 - val_loss: 0.9713 - val_mae: 0.6070 - val_mse: 0.9713
Epoch 6/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.7705 - mae: 0.5774 - mse: 0.7705 - val_loss: 0.7185 - val_mae: 0.5142 - val_mse: 0.7185
Epoch 7/60

56/56 [==============================] - 0s 1ms/step - loss: 0.4161 - mae: 0.3753 - mse: 0.4161 - val_loss: 0.4438 - val_mae: 0.3580 - val_mse: 0.4438
Epoch 100/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.4147 - mae: 0.3711 - mse: 0.4147 - val_loss: 0.4472 - val_mae: 0.3866 - val_mse: 0.4472
Epoch 101/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.4145 - mae: 0.3743 - mse: 0.4145 - val_loss: 0.4497 - val_mae: 0.3589 - val_mse: 0.4497
Epoch 102/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.4130 - mae: 0.3712 - mse: 0.4130 - val_loss: 0.4397 - val_mae: 0.3557 - val_mse: 0.4397
Epoch 103/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.4103 - mae: 0.3692 - mse: 0.4103 - val_loss: 0.4404 - val_mae: 0.3718 - val_mse: 0.4404
Epoch 104/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.4117 - mae: 0.3724 - mse: 0.4117 - val_loss: 0.4538 - val_mae: 0.3574 - val_mse: 0.4538
Epoch 105/6000

56/56 [==============================] - 0s 1ms/step - loss: 0.3414 - mae: 0.3365 - mse: 0.3414 - val_loss: 0.3649 - val_mae: 0.3190 - val_mse: 0.3649
Epoch 198/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.3361 - mae: 0.3332 - mse: 0.3361 - val_loss: 0.3768 - val_mae: 0.3204 - val_mse: 0.3768
Epoch 199/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.3345 - mae: 0.3334 - mse: 0.3345 - val_loss: 0.3628 - val_mae: 0.3275 - val_mse: 0.3628
Epoch 200/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.3401 - mae: 0.3346 - mse: 0.3401 - val_loss: 0.3661 - val_mae: 0.3184 - val_mse: 0.3661
Epoch 201/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.3404 - mae: 0.3327 - mse: 0.3404 - val_loss: 0.3643 - val_mae: 0.3365 - val_mse: 0.3643
Epoch 202/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.3366 - mae: 0.3309 - mse: 0.3366 - val_loss: 0.3840 - val_mae: 0.3214 - val_mse: 0.3840
Epoch 203/6000

56/56 [==============================] - 0s 1ms/step - loss: 0.2252 - mae: 0.2596 - mse: 0.2252 - val_loss: 0.2600 - val_mae: 0.2539 - val_mse: 0.2600
Epoch 296/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.2247 - mae: 0.2590 - mse: 0.2247 - val_loss: 0.2578 - val_mae: 0.2540 - val_mse: 0.2578
Epoch 297/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.2251 - mae: 0.2595 - mse: 0.2251 - val_loss: 0.2590 - val_mae: 0.2530 - val_mse: 0.2590
Epoch 298/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.2234 - mae: 0.2581 - mse: 0.2234 - val_loss: 0.2566 - val_mae: 0.2559 - val_mse: 0.2566
Epoch 299/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.2231 - mae: 0.2578 - mse: 0.2231 - val_loss: 0.2561 - val_mae: 0.2539 - val_mse: 0.2561
Epoch 300/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.2228 - mae: 0.2579 - mse: 0.2228 - val_loss: 0.2569 - val_mae: 0.2519 - val_mse: 0.2569
Epoch 301/6000

56/56 [==============================] - 0s 1ms/step - loss: 0.1906 - mae: 0.2361 - mse: 0.1906 - val_loss: 0.2237 - val_mae: 0.2329 - val_mse: 0.2237
Epoch 394/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.1899 - mae: 0.2359 - mse: 0.1899 - val_loss: 0.2229 - val_mae: 0.2333 - val_mse: 0.2229
Epoch 395/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.1909 - mae: 0.2371 - mse: 0.1909 - val_loss: 0.2238 - val_mae: 0.2316 - val_mse: 0.2238
Epoch 396/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.1904 - mae: 0.2359 - mse: 0.1904 - val_loss: 0.2244 - val_mae: 0.2373 - val_mse: 0.2244
Epoch 397/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.1892 - mae: 0.2354 - mse: 0.1892 - val_loss: 0.2226 - val_mae: 0.2318 - val_mse: 0.2226
Epoch 398/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.1892 - mae: 0.2345 - mse: 0.1892 - val_loss: 0.2240 - val_mae: 0.2380 - val_mse: 0.2240
Epoch 399/6000

...

56/56 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1262 - mse: 0.0799 - val_loss: 0.1179 - val_mae: 0.1328 - val_mse: 0.1179
Epoch 36590/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0798 - mae: 0.1265 - mse: 0.0798 - val_loss: 0.1187 - val_mae: 0.1316 - val_mse: 0.1187
Epoch 36591/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1263 - mse: 0.0799 - val_loss: 0.1184 - val_mae: 0.1317 - val_mse: 0.1184
Epoch 36592/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1257 - mse: 0.0797 - val_loss: 0.1182 - val_mae: 0.1317 - val_mse: 0.1182
Epoch 36593/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1259 - mse: 0.0797 - val_loss: 0.1181 - val_mae: 0.1319 - val_mse: 0.1181
Epoch 36594/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1259 - mse: 0.0797 - val_loss: 0.1182 - val_mae: 0.1318 - val_mse: 0.1182
Epoc

56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1258 - mse: 0.0797 - val_loss: 0.1183 - val_mae: 0.1319 - val_mse: 0.1183
Epoch 36686/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1265 - mse: 0.0799 - val_loss: 0.1198 - val_mae: 0.1324 - val_mse: 0.1198
Epoch 36687/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0798 - mae: 0.1261 - mse: 0.0798 - val_loss: 0.1188 - val_mae: 0.1318 - val_mse: 0.1188
Epoch 36688/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1258 - mse: 0.0797 - val_loss: 0.1180 - val_mae: 0.1320 - val_mse: 0.1180
Epoch 36689/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0798 - mae: 0.1261 - mse: 0.0798 - val_loss: 0.1180 - val_mae: 0.1317 - val_mse: 0.1180
Epoch 36690/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1259 - mse: 0.0797 - val_loss: 0.1191 - val_mae: 0.1320 - val_mse: 0.1191
Epoc

56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1261 - mse: 0.0797 - val_loss: 0.1197 - val_mae: 0.1325 - val_mse: 0.1197
Epoch 36782/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0798 - mae: 0.1260 - mse: 0.0798 - val_loss: 0.1181 - val_mae: 0.1319 - val_mse: 0.1181
Epoch 36783/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0795 - mae: 0.1257 - mse: 0.0795 - val_loss: 0.1184 - val_mae: 0.1313 - val_mse: 0.1184
Epoch 36784/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1254 - mse: 0.0796 - val_loss: 0.1194 - val_mae: 0.1321 - val_mse: 0.1194
Epoch 36785/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1258 - mse: 0.0796 - val_loss: 0.1179 - val_mae: 0.1318 - val_mse: 0.1179
Epoch 36786/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1258 - mse: 0.0797 - val_loss: 0.1180 - val_mae: 0.1320 - val_mse: 0.1180
Epoc

56/56 [==============================] - 0s 1ms/step - loss: 0.0795 - mae: 0.1257 - mse: 0.0795 - val_loss: 0.1180 - val_mae: 0.1317 - val_mse: 0.1180
Epoch 36878/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1262 - mse: 0.0797 - val_loss: 0.1180 - val_mae: 0.1319 - val_mse: 0.1180
Epoch 36879/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1262 - mse: 0.0799 - val_loss: 0.1189 - val_mae: 0.1319 - val_mse: 0.1189
Epoch 36880/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1256 - mse: 0.0796 - val_loss: 0.1186 - val_mae: 0.1317 - val_mse: 0.1186
Epoch 36881/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1260 - mse: 0.0797 - val_loss: 0.1177 - val_mae: 0.1329 - val_mse: 0.1177
Epoch 36882/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1264 - mse: 0.0797 - val_loss: 0.1191 - val_mae: 0.1318 - val_mse: 0.1191
Epoc

56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1258 - mse: 0.0796 - val_loss: 0.1181 - val_mae: 0.1317 - val_mse: 0.1181
Epoch 36974/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0795 - mae: 0.1259 - mse: 0.0795 - val_loss: 0.1178 - val_mae: 0.1345 - val_mse: 0.1178
Epoch 36975/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1259 - mse: 0.0797 - val_loss: 0.1184 - val_mae: 0.1315 - val_mse: 0.1184
Epoch 36976/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1261 - mse: 0.0796 - val_loss: 0.1186 - val_mae: 0.1316 - val_mse: 0.1186
Epoch 36977/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1259 - mse: 0.0796 - val_loss: 0.1180 - val_mae: 0.1318 - val_mse: 0.1180
Epoch 36978/60000
56/56 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1259 - mse: 0.0796 - val_loss: 0.1177 - val_mae: 0.1323 - val_mse: 0.1177
Epoc

In [ ]:
def plot_history(history):
  hist = pd.DataFrame(history.history)
  hist['epoch'] = history.epoch

  plt.figure()
  plt.xlabel('Epoch')
  plt.ylabel('Mean Abs Error')
  plt.plot(hist['epoch'], hist['mae'], label='Train Error')
  plt.plot(hist['epoch'], hist['val_mae'], label='Val Error')
  plt.legend()
  
  plt.figure()
  plt.xlabel('Epoch')
  plt.ylabel('Mean mse Error')
  plt.plot(hist['epoch'], hist['mse'], label='Train Error')
  plt.plot(hist['epoch'], hist['val_mse'], label='Val Error')
  plt.legend()

plot_history(history)  


In [ ]:
pre = model.predict(X_test)
y = y_test
# k = 2
# pre = pre[0]
# y = y[0]

cnt=0
for i in range(len(pre)):
#       print(y[i],'\t', pre[i],'\t', abs(y[i] - pre[i]))
      cnt = cnt + abs(y[i] - pre[i])
print('Abs Error :', cnt)
print('ERROR :', metrics.mean_absolute_error(y,pre))


# for k in range(6):
#     for i in range(len(pre)):
#     #   print(y[i][k],'\t', pre[i][k],'\t', abs(y[i][k] - pre[i][k]))
#       cnt = cnt + abs(y[i][k] - pre[i][k])
#     print('Abs Error :', cnt)  

In [ ]:
for l in range(6):
    print(tar[l], metrics.r2_score(y[:,l], pre[:,l]))

    plt.figure(figsize=(10,10))
    sns.regplot(x=y[:,l], y=pre[:,l])

In [ ]:
y